In [83]:
import os
import sys
import pandas as pd
import numpy as np
sys.path.append('../../')
from deepfold.data.utils.ontology import Ontology
from tools.evaluate_diamondscore import get_diamond_preds, get_diamond_scores
from tools.evaluate_deepmodel import get_model_preds
from sklearn.metrics import f1_score, recall_score, precision_score

In [84]:
base_path = '/home/niejianzheng/xbiome/datasets/protein'
# 存储所有数据文件路径
data_ls = os.walk(base_path).__next__()[2]
data_path_dict = {}
for data in data_ls:
    file_name = data.split('.')[0] + '_' + data.split('.')[1]
    data_path_dict[file_name] = os.path.join(base_path, data)

In [85]:
data_path_dict

{'test_data_fa': '/home/niejianzheng/xbiome/datasets/protein/test_data.fa',
 'uniprot_sprot_dat': '/home/niejianzheng/xbiome/datasets/protein/uniprot_sprot.dat',
 'test_emb_h5': '/home/niejianzheng/xbiome/datasets/protein/test_emb.h5',
 'test_diamond_res': '/home/niejianzheng/xbiome/datasets/protein/test_diamond.res',
 'test_data_pkl': '/home/niejianzheng/xbiome/datasets/protein/test_data.pkl',
 'go_obo': '/home/niejianzheng/xbiome/datasets/protein/go.obo',
 'train_data_pkl': '/home/niejianzheng/xbiome/datasets/protein/train_data.pkl',
 'esm1b_t33_650M_UR50S_embeddings_mean_train_pkl': '/home/niejianzheng/xbiome/datasets/protein/esm1b_t33_650M_UR50S_embeddings_mean_train.pkl',
 'test_annotations_txt': '/home/niejianzheng/xbiome/datasets/protein/test_annotations.txt',
 'train_data_dmnd': '/home/niejianzheng/xbiome/datasets/protein/train_data.dmnd',
 'predictions_pkl': '/home/niejianzheng/xbiome/datasets/protein/predictions.pkl',
 'train_annotations_txt': '/home/niejianzheng/xbiome/datas

In [86]:
go_rels = Ontology(data_path_dict['go_obo'], with_rels=True)

train_df = pd.read_pickle(data_path_dict['train_data_pkl'])
annotations = train_df['prop_annotations'].values
annotations = list(map(lambda x: set(x), annotations))

test_df = pd.read_pickle(data_path_dict['test_data_pkl'])
test_annotations = test_df['prop_annotations'].values
test_annotations = list(map(lambda x: set(x), test_annotations))
go_rels.calculate_ic(annotations + test_annotations)


In [87]:
test_df.head()

index     proteins                       accessions  \
1253     6710   ACK1_YEAST                  Q07622; D6VRF1;   
33330  210625  KIFC1_CRIGR                          Q60443;   
18394  109472   DSC3_HUMAN  Q14574; A6NN35; Q14200; Q9HAZ9;   
95        687   2AAA_SCHPO                  Q9UT08; Q10293;   
11368   62522  CH1CO_SYNAS                          Q2LQN9;   

                                               sequences  \
1253   MVNQGQPQPNLYDKHINMFPPARARESSHKLGNANSDRHGLPAQNI...   
33330  MKEALEPAKKRTRGLGAVTKIDTSRSKGPLLSSLSQPQGPTAAQKG...   
18394  MAAAGPRRSVRGAVCLHLLLTLVIFSRAGEACKKVILNVPSKLEAD...   
95     MQTENQVNDLYPIAVLIDELKHDEITYRLNALERLSTIALALGPER...   
11368  MKGPIKFNALSLQGRSVMSNQSNDTTITQRRDTMNELTEEQKLLME...   

                                             annotations  \
1253   [GO:0005739|HDA, GO:0008047|IBA, GO:0031505|IM...   
33330  [GO:0005769|IEA, GO:0005874|IEA, GO:0005815|IE...   
18394  [GO:0030054|IDA, GO:0005911|IBA, GO:0001533|TA...   
95     [GO:0005737|IBA, GO:0005829|HDA, GO:0090443|ID...   
11368  [GO:0003995|IEA, GO:0050660|IDA, GO:0052890|ID...   

                                               interpros    orgs  \
1253                              [IPR006597, IPR011990]  559292   
33330       [IPR019821, IPR001752, IPR036961, IPR027417]   10029   
18394  [IPR002126, IPR015919, IPR020894, IPR000233, I...    9606   
95          [IPR011989, IPR016024, IPR000357, IPR021133]  284812   
11368  [IPR006089, IPR006091, IPR036250, IPR009075, I...   56780   

                                         exp_annotations  \
1253                [GO:0005739, GO:0031505, GO:0009967]   
33330                                       [GO:0030496]   
18394  [GO:0030054, GO:0001533, GO:0016020, GO:000588...   
95     [GO:0005829, GO:0090443, GO:0110085, GO:004473...   
11368               [GO:0050660, GO:0052890, GO:0051262]   

                                        prop_annotations  cafa_target  
1253   [GO:0043227, GO:0005737, GO:0110165, GO:003150...         True  
33330               [GO:0110165, GO:0005575, GO:0030496]        False  
18394  [GO:0009913, GO:0140096, GO:0022610, GO:004358...         True  
95     [GO:0043227, GO:0022402, GO:0035556, GO:004578...         True  
11368  [GO:0043167, GO:1901363, GO:0051262, GO:005125...        False

## Diamond model

In [88]:

diamond_scores = get_diamond_scores(data_path_dict['test_diamond_res'])
blast_preds = get_diamond_preds(train_df, test_df, diamond_scores)

## DeeGoPlus Model

In [89]:
predictions = pd.read_pickle(data_path_dict['predictions_pkl'])

terms_df = pd.read_pickle(data_path_dict['terms_pkl'])
terms = terms_df['terms'].values.flatten()

ics = {}
for term in terms:
    ics[term] = go_rels.get_ic(term)

prot_index = {}
for i, row in enumerate(train_df.itertuples()):
    prot_index[row.proteins] = i



In [90]:
predictions['prot_len'] = predictions['sequences'].str.len()
predictions.head()

index     proteins                       accessions  \
1253     6710   ACK1_YEAST                  Q07622; D6VRF1;   
33330  210625  KIFC1_CRIGR                          Q60443;   
18394  109472   DSC3_HUMAN  Q14574; A6NN35; Q14200; Q9HAZ9;   
95        687   2AAA_SCHPO                  Q9UT08; Q10293;   
11368   62522  CH1CO_SYNAS                          Q2LQN9;   

                                               sequences  \
1253   MVNQGQPQPNLYDKHINMFPPARARESSHKLGNANSDRHGLPAQNI...   
33330  MKEALEPAKKRTRGLGAVTKIDTSRSKGPLLSSLSQPQGPTAAQKG...   
18394  MAAAGPRRSVRGAVCLHLLLTLVIFSRAGEACKKVILNVPSKLEAD...   
95     MQTENQVNDLYPIAVLIDELKHDEITYRLNALERLSTIALALGPER...   
11368  MKGPIKFNALSLQGRSVMSNQSNDTTITQRRDTMNELTEEQKLLME...   

                                             annotations  \
1253   [GO:0005739|HDA, GO:0008047|IBA, GO:0031505|IM...   
33330  [GO:0005769|IEA, GO:0005874|IEA, GO:0005815|IE...   
18394  [GO:0030054|IDA, GO:0005911|IBA, GO:0001533|TA...   
95     [GO:0005737|IBA, GO:0005829|HDA, GO:0090443|ID...   
11368  [GO:0003995|IEA, GO:0050660|IDA, GO:0052890|ID...   

                                               interpros    orgs  \
1253                              [IPR006597, IPR011990]  559292   
33330       [IPR019821, IPR001752, IPR036961, IPR027417]   10029   
18394  [IPR002126, IPR015919, IPR020894, IPR000233, I...    9606   
95          [IPR011989, IPR016024, IPR000357, IPR021133]  284812   
11368  [IPR006089, IPR006091, IPR036250, IPR009075, I...   56780   

                                         exp_annotations  \
1253                [GO:0005739, GO:0031505, GO:0009967]   
33330                                       [GO:0030496]   
18394  [GO:0030054, GO:0001533, GO:0016020, GO:000588...   
95     [GO:0005829, GO:0090443, GO:0110085, GO:004473...   
11368               [GO:0050660, GO:0052890, GO:0051262]   

                                        prop_annotations  cafa_target  \
1253   [GO:0043227, GO:0005737, GO:0110165, GO:003150...         True   
33330               [GO:0110165, GO:0005575, GO:0030496]        False   
18394  [GO:0009913, GO:0140096, GO:0022610, GO:004358...         True   
95     [GO:0043227, GO:0022402, GO:0035556, GO:004578...         True   
11368  [GO:0043167, GO:1901363, GO:0051262, GO:005125...        False   

                                                  labels  \
1253   [1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, ...   
33330  [1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, ...   
18394  [1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, ...   
95     [1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, ...   
11368  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   

                                                   preds  prot_len  
1253   [0.9028676, 0.012715803, 0.0014727293, 0.00745...       623  
33330  [0.9455861, 0.0015807436, 3.999437e-05, 0.0003...       622  
18394  [0.8087489, 0.0016527537, 0.00028462024, 0.000...       896  
95     [0.9657183, 0.0043522124, 0.0008709415, 0.0034...       590  
11368  [0.13663456, 0.00061553024, 0.00029366414, 0.0...       414

In [91]:
def annotations_to_multilabel(annotations, terms):
    multilabels = []
    terms_dict = {prot:idx for idx, prot in enumerate(terms)}
    for prot_anno in annotations:
        multi_label = [0] * len(terms)
        for go_term in  prot_anno:
            if go_term in terms_dict:
                multi_label[terms_dict[go_term]] = 1
        multilabels.append(multi_label)
    return  multilabels

In [92]:
train_annotations = train_df['prop_annotations'].tolist()
train_multilabels = annotations_to_multilabel(train_annotations, terms)

## threshold = 0.2

In [93]:
def get_diamond_preds_multilabel(blast_preds, terms):
    diamond_preds = []
    terms_dict = {prot:idx for idx, prot in enumerate(terms)}
    for protein_res in blast_preds:
        multi_label = [0] * len(terms)
        for prot_id, score in protein_res.items():
            if prot_id in terms_dict:
                idx = terms_dict[prot_id]
                multi_label[int(idx)] = score
        diamond_preds.append(multi_label)
    return  diamond_preds

In [94]:
def idx_to_term(preds, terms, threshod):
    model_preds = []
    for prot_pred in preds:
        term_name_list = terms[prot_pred > threshod]
        model_preds.append(term_name_list)
    return model_preds

In [95]:
def filter_preds_multilabel(preds, threshold):
    filter_res = []
    for pred in preds:
        res = [1 if pp > threshold else 0 for pp in pred]
        filter_res.append(res)
    return filter_res

def filter_preds(preds, threshold):
    filter_res = []
    for pred in preds:
        res = [k for k,v in pred.items() if v > threshold]
        filter_res.append(res)
    return  filter_res

In [96]:
blast_preds_multilabel = get_diamond_preds_multilabel(blast_preds, terms)
blast_preds_multilabel = filter_preds_multilabel(blast_preds_multilabel, threshold=0.2)
blast_preds_filter = filter_preds(blast_preds, threshold=0.2)

In [97]:
model_preds = get_model_preds(predictions, terms)
model_preds_filter = filter_preds(model_preds, threshold=0.2)
model_pred_multilabel = predictions['preds'].tolist()
model_pred_multilabel = filter_preds_multilabel(model_pred_multilabel, threshold=0.2)
predictions['model_pred_multilabel'] = list(model_pred_multilabel)
predictions['model_preds'] = list(model_preds_filter)

In [98]:
predictions['blast_pred_multilabel'] = list(blast_preds_multilabel)
predictions['blast_preds'] = list(blast_preds_filter)

In [99]:
predictions.head()

index     proteins                       accessions  \
1253     6710   ACK1_YEAST                  Q07622; D6VRF1;   
33330  210625  KIFC1_CRIGR                          Q60443;   
18394  109472   DSC3_HUMAN  Q14574; A6NN35; Q14200; Q9HAZ9;   
95        687   2AAA_SCHPO                  Q9UT08; Q10293;   
11368   62522  CH1CO_SYNAS                          Q2LQN9;   

                                               sequences  \
1253   MVNQGQPQPNLYDKHINMFPPARARESSHKLGNANSDRHGLPAQNI...   
33330  MKEALEPAKKRTRGLGAVTKIDTSRSKGPLLSSLSQPQGPTAAQKG...   
18394  MAAAGPRRSVRGAVCLHLLLTLVIFSRAGEACKKVILNVPSKLEAD...   
95     MQTENQVNDLYPIAVLIDELKHDEITYRLNALERLSTIALALGPER...   
11368  MKGPIKFNALSLQGRSVMSNQSNDTTITQRRDTMNELTEEQKLLME...   

                                             annotations  \
1253   [GO:0005739|HDA, GO:0008047|IBA, GO:0031505|IM...   
33330  [GO:0005769|IEA, GO:0005874|IEA, GO:0005815|IE...   
18394  [GO:0030054|IDA, GO:0005911|IBA, GO:0001533|TA...   
95     [GO:0005737|IBA, GO:0005829|HDA, GO:0090443|ID...   
11368  [GO:0003995|IEA, GO:0050660|IDA, GO:0052890|ID...   

                                               interpros    orgs  \
1253                              [IPR006597, IPR011990]  559292   
33330       [IPR019821, IPR001752, IPR036961, IPR027417]   10029   
18394  [IPR002126, IPR015919, IPR020894, IPR000233, I...    9606   
95          [IPR011989, IPR016024, IPR000357, IPR021133]  284812   
11368  [IPR006089, IPR006091, IPR036250, IPR009075, I...   56780   

                                         exp_annotations  \
1253                [GO:0005739, GO:0031505, GO:0009967]   
33330                                       [GO:0030496]   
18394  [GO:0030054, GO:0001533, GO:0016020, GO:000588...   
95     [GO:0005829, GO:0090443, GO:0110085, GO:004473...   
11368               [GO:0050660, GO:0052890, GO:0051262]   

                                        prop_annotations  cafa_target  \
1253   [GO:0043227, GO:0005737, GO:0110165, GO:003150...         True   
33330               [GO:0110165, GO:0005575, GO:0030496]        False   
18394  [GO:0009913, GO:0140096, GO:0022610, GO:004358...         True   
95     [GO:0043227, GO:0022402, GO:0035556, GO:004578...         True   
11368  [GO:0043167, GO:1901363, GO:0051262, GO:005125...        False   

                                                  labels  \
1253   [1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, ...   
33330  [1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, ...   
18394  [1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, ...   
95     [1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, ...   
11368  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   

                                                   preds  prot_len  \
1253   [0.9028676, 0.012715803, 0.0014727293, 0.00745...       623   
33330  [0.9455861, 0.0015807436, 3.999437e-05, 0.0003...       622   
18394  [0.8087489, 0.0016527537, 0.00028462024, 0.000...       896   
95     [0.9657183, 0.0043522124, 0.0008709415, 0.0034...       590   
11368  [0.13663456, 0.00061553024, 0.00029366414, 0.0...       414   

                                   model_pred_multilabel  \
1253   [1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
33330  [1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
18394  [1, 0, 0, 0, 0, 1, 0, 0, 0, 1, 1, 1, 0, 0, 1, ...   
95     [1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
11368  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                             model_preds  \
1253   [GO:0110165, GO:0005575, GO:0003674, GO:000815...   
33330  [GO:0110165, GO:0005575, GO:0003674, GO:000815...   
18394  [GO:0110165, GO:0005575, GO:0032501, GO:000727...   
95     [GO:0110165, GO:0005575, GO:0003674, GO:002241...   
11368  [GO:0003674, GO:0008150, GO:0043167, GO:190136...   

                                   blast_pred_multilabel  \
1253   [1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
33330  [1, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 1, 0, 0, 0, ...   
18394  [1, 0, 

In [100]:
def compute_acc(labels, preds):
    scores = []
    for label, pred in zip(labels, preds):
        acc = precision_score(label, pred)
        scores.append(acc)
    return scores

def compute_recall(labels, preds):
    scores = []
    for label, pred in zip(labels, preds):
        acc = recall_score(label, pred)
        scores.append(acc)
    return scores


def compute_f1score(labels, preds):
    scores = []
    for label, pred in zip(labels, preds):
        acc = f1_score(label, pred)
        scores.append(acc)
    return scores

# GO Term Analysis

In [101]:
multilabels = predictions['labels'].tolist()
blast_pred_multilabel = predictions['blast_pred_multilabel'].tolist()
model_pred_multilabel = predictions['model_pred_multilabel'].tolist()


blast_preds_multilabel = np.stack(blast_pred_multilabel, axis=0).transpose().tolist()
model_pred_multilabel = np.stack(model_pred_multilabel, axis=0).transpose().tolist()
multilabels = np.stack(multilabels, axis=0).transpose().tolist()
train_multilabels = np.stack(train_multilabels, axis=0).transpose().tolist()

In [102]:
model_pred_acc = compute_acc(multilabels, model_pred_multilabel)
blast_pred_acc = compute_acc(multilabels, blast_preds_multilabel)

model_pred_recall = compute_recall(multilabels, model_pred_multilabel)
blast_pred_recall = compute_recall(multilabels, blast_preds_multilabel)

model_pred_f1score = compute_f1score(multilabels, model_pred_multilabel)
blast_pred_f1score = compute_f1score(multilabels, blast_preds_multilabel)

terms = terms_df['terms'].values.flatten()

/home/niejianzheng/anaconda3/envs/pytorch/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning:

Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.

/home/niejianzheng/anaconda3/envs/pytorch/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning:

Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.

/home/niejianzheng/anaconda3/envs/pytorch/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning:

Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.

/home/niejianzheng/anaconda3/envs/pytorch/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning:

Precision is ill-defined and being set to 0.0 due to no pred

In [103]:
df = pd.DataFrame(zip(model_pred_acc, blast_pred_acc, model_pred_recall,
                      blast_pred_recall, model_pred_f1score,
                      blast_pred_f1score),
                  index=list(terms),
                  columns=[
                      'model_acc', 'blast_acc', 'model_recall', 'blast_recall',
                      'model_f1_score', 'blast_f1_score'
                  ])
go_samples = [sum(multilabel) for multilabel in train_multilabels]
df['go_samples'] = go_samples

In [104]:
df.head()

model_acc  blast_acc  model_recall  blast_recall  model_f1_score  \
GO:0110165   0.764186   0.775206      0.995120      0.887069        0.864497   
GO:0018995   0.111111   0.150000      0.125000      0.125000        0.117647   
GO:0030430   0.000000   0.250000      0.000000      0.090909        0.000000   
GO:0033643   0.058824   0.300000      0.045455      0.136364        0.051282   
GO:0043656   0.105263   0.300000      0.125000      0.187500        0.114286   

            blast_f1_score  go_samples  
GO:0110165        0.827373       55263  
GO:0018995        0.136364         470  
GO:0030430        0.133333         171  
GO:0033643        0.187500         344  
GO:0043656        0.230769         261

In [105]:
def compute_score(series):
    model_acc = series["model_acc"]
    blast_acc = series["blast_acc"]
    model_recall = series['model_recall']
    blast_recall = series['blast_recall']
    if blast_acc > model_acc and blast_recall > model_recall:
        return "blast_acc > model_acc & blast_recall > model_recall"
    elif blast_acc >model_acc and blast_recall < model_recall:
        return "blast_acc > model_acc and blast_recall < model_recall"
    elif blast_acc < model_acc and blast_recall > model_recall:
        return "blast_acc < model_acc and blast_recall > model_recall"
    else:
        return "blast_acc < model_acc and blast_recall < model_recall"


df["score"] = df.apply(compute_score,axis=1)
df.head()

model_acc  blast_acc  model_recall  blast_recall  model_f1_score  \
GO:0110165   0.764186   0.775206      0.995120      0.887069        0.864497   
GO:0018995   0.111111   0.150000      0.125000      0.125000        0.117647   
GO:0030430   0.000000   0.250000      0.000000      0.090909        0.000000   
GO:0033643   0.058824   0.300000      0.045455      0.136364        0.051282   
GO:0043656   0.105263   0.300000      0.125000      0.187500        0.114286   

            blast_f1_score  go_samples  \
GO:0110165        0.827373       55263   
GO:0018995        0.136364         470   
GO:0030430        0.133333         171   
GO:0033643        0.187500         344   
GO:0043656        0.230769         261   

                                                        score  
GO:0110165  blast_acc > model_acc and blast_recall < model...  
GO:0018995  blast_acc < model_acc and blast_recall < model...  
GO:0030430  blast_acc > model_acc & blast_recall > model_r...  
GO:0033643  blast_acc > model_acc & blast_recall > model_r...  
GO:0043656  blast_acc > model_acc & blast_recall > model_r...

In [106]:
import plotly.express as px
fig = px.scatter(df, x="blast_acc", y="model_acc", hover_data=[df.index], width=800, height=800)
fig.add_shape(type="line",
    xref="x", yref="y",
    x0=0, y0=0, x1=1, y1=1,  # 相对坐标
    line=dict(
        color="black",
        width=3,
    ),
)
fig.show()

In [107]:
import plotly.express as px
fig = px.scatter(df, x="blast_recall", y="model_recall",  hover_data=[df.index], width=800, height=800)
fig.add_shape(type="line",
    xref="x", yref="y",
    x0=0, y0=0, x1=1, y1=1,  # 相对坐标
    line=dict(
        color="red",
        width=3,
    ),
)
fig.show()

In [108]:
import plotly.express as px
fig = px.scatter(df, x="blast_f1_score", y="model_f1_score",  color="score",  hover_data=[df.index],  width=1200, height=800)
fig.add_shape(type="line",
    xref="x", yref="y",
    x0=0, y0=0, x1=1, y1=1,  # 相对坐标
    line=dict(
        color="red",
        width=3,
    ),
)
fig.show()

In [109]:
df2 = df[df.model_f1_score < 0.0001]
df2.head()


model_acc  blast_acc  model_recall  blast_recall  model_f1_score  \
GO:0030430        0.0   0.250000           0.0      0.090909             0.0   
GO:0071695        0.0   0.129032           0.0      0.125000             0.0   
GO:0010431        0.0   0.333333           0.0      0.333333             0.0   
GO:0021700        0.0   0.142857           0.0      0.125000             0.0   
GO:0071367        0.0   0.250000           0.0      0.333333             0.0   

            blast_f1_score  go_samples  \
GO:0030430        0.133333         171   
GO:0071695        0.126984         662   
GO:0010431        0.333333          83   
GO:0021700        0.133333         751   
GO:0071367        0.285714          68   

                                                        score  
GO:0030430  blast_acc > model_acc & blast_recall > model_r...  
GO:0071695  blast_acc > model_acc & blast_recall > model_r...  
GO:0010431  blast_acc > model_acc & blast_recall > model_r...  
GO:0021700  blast_acc > model_acc & blast_recall > model_r...  
GO:0071367  blast_acc > model_acc & blast_recall > model_r...

In [110]:
import plotly.express as px

fig = px.histogram(df2, x="go_samples")
fig.show()

In [112]:
bins = [0, 50, 100, 200, 500, 1000, 2000, 100000]
df['Categories'] = pd.cut(df['go_samples'], bins, labels=['0~50', '50~100' ,'100~200', '200~500', '500~1000', '1000~2000', '2000~100000'])
df.head(4)

df1 = df.groupby("Categories").agg('mean')
df1['go_samples'] = ['0~50', '50~100', '100~200', '200~500', '500~1000', '1000~2000', '2000~100000']
df1


model_acc  blast_acc  model_recall  blast_recall  model_f1_score  \
Categories                                                                      
0~50          0.186075   0.226712      0.150889      0.277773        0.152467   
50~100        0.166471   0.201038      0.126123      0.257708        0.127487   
100~200       0.234759   0.217904      0.165231      0.280991        0.172160   
200~500       0.296324   0.238951      0.212272      0.315017        0.226162   
500~1000      0.328732   0.264210      0.269398      0.361673        0.278895   
1000~2000     0.341008   0.280787      0.317745      0.414955        0.320077   
2000~100000   0.388910   0.352723      0.518265      0.556462        0.438451   

             blast_f1_score   go_samples  
Categories                                
0~50               0.227962         0~50  
50~100             0.204034       50~100  
100~200            0.229687      100~200  
200~500            0.261141      200~500  
500~1000           0.300286     500~1000  
1000~2000          0.332356    1000~2000  
2000~100000        0.430282  2000~100000

In [113]:
import plotly.express as px
import plotly.graph_objects as go

fig = px.scatter(df, x="go_samples", y="model_f1_score",  hover_data=[df.index],  width=600, height=400)
fig.show()

In [114]:
fig = px.scatter(df, x="go_samples", y="blast_f1_score",  hover_data=[df.index],  width=600, height=400)
fig.show()

In [115]:
fig = px.bar(df1, x="go_samples",y="blast_f1_score",  width=600, height=400)
fig.show()

In [116]:
fig = px.bar(df1, x="go_samples", y="model_f1_score",  width=600, height=400)
fig.show()

In [117]:

import plotly.graph_objects as go

prot_len = df1['go_samples'].tolist()

fig = go.Figure(data=[
    go.Bar(name='model_f1_score', x=prot_len, y=df1['model_f1_score'].tolist()),
    go.Bar(name='blast_f1_score', x=prot_len, y=df1['blast_f1_score'].tolist()),
])
fig.update_layout(barmode='group')
fig.show()

In [118]:

import plotly.graph_objects as go

prot_len = df1['go_samples'].tolist()

fig = go.Figure(data=[
    go.Bar(name='model_acc', x=prot_len, y=df1['model_acc'].tolist()),
    go.Bar(name='blast_acc', x=prot_len, y=df1['blast_acc'].tolist()),
])
fig.update_layout(barmode='group')
fig.show()

In [119]:

import plotly.graph_objects as go

prot_len = df1['go_samples'].tolist()

fig = go.Figure(data=[
    go.Bar(name='model_recall', x=prot_len, y=df1['model_recall'].tolist()),
    go.Bar(name='blast_recall', x=prot_len, y=df1['blast_recall'].tolist()),
])
fig.update_layout(barmode='group')
fig.show()